In [4]:
import pandas as pd
from ensemble_boxes import *

In [6]:
df1 = pd.read_csv('/data/ephemeral/home/level2-objectdetection-cv-10/develop/yumin/mmdetection/work_dirs/swin_b_trash/submission_epoch_14.csv')
df2 = pd.read_csv('/data/ephemeral/home/level2-objectdetection-cv-10/develop/yumin/mmdetection/work_dirs/cascade_rcnn_r50_fpn_1x_swin_trash/submission_epoch_30.csv')

In [7]:
df1

PredictionString       image_id
0     0 0.121960044 482.9039 583.99866 565.7565 653....  test/0000.jpg
1     0 0.8027691 640.4309 648.95856 685.1786 825.75...  test/0001.jpg
2     0 0.48348117 874.63104 458.2091 1016.5335 626....  test/0002.jpg
3     9 0.98175335 128.5305 269.39792 932.4219 820.0...  test/0003.jpg
4     0 0.30816063 466.18857 412.47626 660.85736 535...  test/0004.jpg
...                                                 ...            ...
4866  0 0.73309 288.9527 352.4161 669.0753 687.4638 ...  test/4866.jpg
4867  0 0.84558123 628.8472 666.69995 772.60126 722....  test/4867.jpg
4868  0 0.115450196 549.86865 522.9759 730.6768 820....  test/4868.jpg
4869  0 0.9067782 2.0403907 203.84254 1007.73517 935...  test/4869.jpg
4870  0 0.27780366 240.85002 822.6493 293.7408 852.5...  test/4870.jpg

[4871 rows x 2 columns]

In [10]:

for info in df1.values:
    classes = []
    scores = []
    boxes = []

    box_info, name = info.split(',')
    boxes = box_info.split()

    classes = [int(boxes [i]) for i in range(0, len(boxes ), 6)]
    scores = [float(boxes [i]) for i in range(1, len(boxes ), 6)]
    boxes = [[float(boxes [i]), float(boxes [i+1]), float(boxes [i+2]), float(boxes [i+3])] for i in range(2, len(boxes ), 6)]

    

['0 0.121960044 482.9039 583.99866 565.7565 653.9299 0 0.055728648 472.99716 573.96954 558.40393 595.34314 1 0.9879325 562.89685 102.43562 766.14435 357.63284 1 0.5077965 639.04944 261.12695 735.6304 343.80106 1 0.28227264 666.83203 262.9877 729.1984 318.39972 1 0.25131416 633.02026 175.1245 749.25415 344.97806 1 0.22384596 239.3563 408.94446 286.25226 435.82718 1 0.15894298 658.31055 187.18282 691.6676 237.91039 1 0.1538104 243.94969 407.48837 280.72958 471.43616 1 0.15156941 170.50511 429.39844 202.40067 450.52524 1 0.14676654 154.11578 425.09546 201.07156 448.781 1 0.13688384 486.85675 592.20844 563.4594 644.4367 1 0.12988712 583.9094 249.64056 743.3971 352.8152 1 0.11844227 470.49368 568.707 569.1632 653.605 1 0.09474307 571.00226 113.21673 728.01196 359.6032 1 0.07795878 472.99716 573.96954 558.40393 595.34314 1 0.06506285 401.90167 448.79114 584.2669 588.4903 1 0.0633302 234.5918 405.26343 336.00772 462.4124 5 0.90926266 241.49326 685.8526 299.7156 748.1702 5 0.70927626 336.54315

In [ ]:
data_string = "0 0.22284965 319.26932 566.3335 388.07785 617.85187 0 0.21063708 210.20618 692.2166 252.05852 732.76056"

# 문자열을 공백을 기준으로 분할
values = data_string.split()

# class 추출
classes = [int(values[i]) for i in range(0, len(values), 6)]

# score 추출
scores = [float(values[i]) for i in range(1, len(values), 6)]

# box 추출
boxes = [[float(values[i]), float(values[i+1]), float(values[i+2]), float(values[i+3])] for i in range(2, len(values), 6)]


In [3]:





def parse_predictions(df):
    boxes = []
    scores = []
    labels = []

    for _, row in df.iterrows():
        prediction = [float(x) for x in row['PredictionString'].split()]
        boxes.append([[prediction[i], prediction[i + 1], prediction[i + 2], prediction[i + 3]] for i in range(2, len(prediction), 6)])
        scores.append([prediction[i] for i in range(1, len(prediction), 6)])
        labels.append([int(prediction[i]) for i in range(0, len(prediction), 6)])

    return boxes, scores, labels

final_predictions = []
for image_id in df1['image_id'].unique():
    boxes1, scores1, labels1 = parse_predictions(df1[df1['image_id'] == image_id])
    boxes2, scores2, labels2 = parse_predictions(df2[df2['image_id'] == image_id])
    # Add more models if necessary

    boxes, scores, labels = weighted_boxes_fusion([boxes1, boxes2], [scores1, scores2], [labels1, labels2])
    final_predictions.append((image_id, boxes, scores, labels))

# 결과를 DataFrame으로 변환
ensemble_df = pd.DataFrame(final_predictions, columns=['image_id', 'boxes', 'scores', 'labels'])

# 각 탐지를 문자열로 변환하여 저장
ensemble_df['PredictionString'] = ensemble_df.apply(lambda x: ' '.join(
    [f"{label} {score} {box[0]} {box[1]} {box[2]} {box[3]}" 
     for label, score, box in zip(x['labels'], x['scores'], x['boxes'])
    ]), axis=1)

# 필요한 열만 선택하여 저장
ensemble_df[['image_id', 'PredictionString']].to_csv('ensemble_out.csv', index=False)


TypeError: '<' not supported between instances of 'list' and 'float'